## get_obs_paths

This notebook reads in a CSV table containing a column of PACS obsids, and adds a column containing the path to the level 2.5 high-pass filtered blue map (in FITS format) corresponding to each observation, where available. This is useful if you have a folder full of data downloaded from *Herschel* Science Archive (HSA) but don't know specifically where the observation you're looking for is located. In particular, the table produced by this notebook can be used as input to the disc modelling code `pacs_model_batch.py`.

The notebook assumes that the data have been downloaded from HSA and placed in some specified root directory, and that the file structure has not been altered following the download &#150; the obsid, level and processing method of a particular image are inferred from its path. It also expects that the input table includes columns `wave` and `star_jy`, containing wavelengths and predicted stellar fluxes for each system at 70/100 μm (i.e. there are at least two rows for each system). For the final output table, the appropriate row will be selected, given the wavelength of the obsid as determined from the FITS file.

### Setup

In [1]:
import pandas as pd
import numpy as np
from astropy.io import fits
from pathlib import Path

In [2]:
#don't truncate path strings when displaying them in a DataFrame
pd.set_option('display.max_colwidth', -1)

#display the full tables
pd.set_option('display.max_rows', None)

### Obtain a list of relevant images

This is achieved by walking recursively through all directories contained in `rootdir` and appending the paths that match the specified pattern to a list. For now, only look for level 2.5 high-pass filtered images.

In [3]:
#all data should be somewhere inside this directory
rootdir = '/data/wyatt_archive/gkennedy/hsa/auto'

#look for files matching this pattern
pattern = '*/level2_5/HPPHPFMAPB/*.fits.gz'

In [4]:
#get the paths of all desired maps within rootdir

paths = []
obsids_from_paths = []
mtimes = []
obs_waves = []

for path in Path(rootdir).rglob(pattern):
    
    full_path = path.resolve()
    paths.append(str(full_path))
    
    #need to go two levels up to get the obsid, given the file structure provided by HSA
    obsids_from_paths.append(int(full_path.parents[2].name))
    
    #append the last modification time, so that we can find the most up-to-date file if duplicates are found
    mtimes.append(path.lstat().st_mtime)
    
    #extract observation wavelength from FITS file
    with fits.open(str(full_path))as datafile:
        obs_waves.append(int(datafile[0].header['WAVELNTH']))

In [5]:
#store the results in a DataFrame, so that we can easily join them onto the provided CSV table
df_paths = pd.DataFrame({'obsid': obsids_from_paths, 'obs_wave': obs_waves, 'path': paths, 'mtime': mtimes},
                        columns = ['obsid', 'obs_wave', 'path', 'mtime'])

#sort by obsid, with the oldest files (i.e. smallest mtimes) at the top
df_paths.sort_values(by = ['obsid', 'mtime'], inplace = True)

In [6]:
#if multiple images were found for a particular obsid, keep only the most recently modified file
df_paths.drop_duplicates(subset = ['obsid'], keep = 'last', inplace = True)

#modification times were only necessary for sorting; drop these now
df_paths.drop(['mtime'], axis = 1, inplace = True)

In [7]:
#look at the final path table
df_paths

obsid  obs_wave  \
8     1342186612  70         
9     1342186619  70         
5     1342187075  100        
6     1342187145  100        
10    1342188369  70         
11    1342188370  70         
12    1342188371  70         
13    1342188372  70         
14    1342188377  70         
15    1342188484  70         
16    1342188506  70         
17    1342188507  70         
18    1342188514  70         
19    1342188516  70         
20    1342188517  70         
21    1342188518  70         
22    1342188854  70         
23    1342188884  70         
24    1342188885  70         
25    1342188887  70         
26    1342189150  70         
27    1342189365  70         
28    1342189367  70         
29    1342189592  70         
30    1342189657  70         
31    1342189658  70         
32    1342189659  70         
33    1342190306  70         
34    1342190345  70         
35    1342190346  70         
36    1342191014  70         
37    1342191015  70         
38    1342191016  70         
39    1342191017  70         
40    1342191018  70         
1786  1342191102  100        
1787  1342191104  70         
228   1342192757  100        
41    1342192759  70         
607   1342192760  100        
608   1342192775  100        
229   1342193038  100        
230   1342193040  100        
231   1342193042  100        
232   1342193046  100        
609   1342193057  100        
233   1342193059  100        
234   1342193061  100        
235   1342193064  100        
236   1342193068  100        
237   1342193105  100        
238   1342193107  100        
239   1342193109  100        
42    1342193111  70         
610   1342193112  100        
240   1342193115  100        
611   1342193117  100        
241   1342193123  100        
43    1342193139  70         
44    1342193140  70         
242   1342193142  100        
243   1342193145  100        
244   1342193147  100        
245   1342193149  100        
246   1342193151  100        
247   1342193153  100        
1788  1342193157  70         
1789  1342193159  100        
248   1342193161  100        
1790  1342193163  70         
1791  1342193165  100        
249   1342193167  100        
250   1342193169  100        
45    1342193502  70         
1792  1342193509  70         
1793  1342193511  100        
251   1342193513  100        
615   1342193515  100        
252   1342193522  100        
1794  1342193526  70         
1795  1342193528  100        
253   1342193530  100        
254   1342193538  100        
46    1342193550  70         
1796  1342194063  70         
1797  1342194065  100        
255   1342194067  100        
256   1342195362  100        
257   1342195364  100        
618   1342195413  100        
7     1342195466  70         
47    1342195469  70         
258   1342195577  100        
259   1342195579  100        
260   1342195581  100        
261   1342195604  100        
262   1342195606  100        
263   1342195608  100        
619   1342195614  100        
1798  1342195696  70         
1799  1342195698  100        
264   1342195700  100        
265   1342195704  100        
621   1342195779  100        
622   1342195781  100        
266   1342195829  100        
267   1342195831  100        
268   1342195835  100        
269   1342196014  100        
270   1342196021  100        
271   1342196032  100        
1     1342196038  70         
272   1342196039  100        
48    1342196104  70         
1800  1342196105  70         
1801  1342196107  100        
273   1342196109  100        
1802  1342196115  70         
1803  1342196117  100        
625   1342196123  100        
626   1342196125  100        
274   1342196127  100        
627   1342196732  100        
628   1342196743  100        
629   1342196747  100        
1804  1342196753  70         
1805  1342196755  100        
631   1342196779  100        
1806  1342196781  70         
1807  1342196783  100        
275   1342196785  100        
1808  1342196787  70         
1809  1342196789  100

### Read in the CSV table 

In [8]:
csv_filename = 'input/obs_list.csv'
df_in = pd.read_csv(csv_filename)

In [9]:
#look at the input table
df_in

obsid                      xid      dist_pc   filter  wave  \
0     1342231387  * 19 LMi                 28.809477    PACS100  100    
1     1342231387  * 19 LMi                 28.809477    PACS70   70     
2     1342237460  * 29 Ari                 28.688807    PACS100  100    
3     1342237460  * 29 Ari                 28.688807    PACS70   70     
4     1342233372  2MASS J08101691-4856291  5055.611729  PACS100  100    
5     1342233372  2MASS J08101691-4856291  5055.611729  PACS70   70     
6     1342265601  CD-54 4621               110.619469   PACS100  100    
7     1342265601  CD-54 4621               110.619469   PACS70   70     
8     1342265609  CD-52 5008               137.741047   PACS100  100    
9     1342265609  CD-52 5008               137.741047   PACS70   70     
10    1342224188  TWA 26                   49.666490    PACS100  100    
11    1342224188  TWA 26                   49.666490    PACS70   70     
12    1342239416  V* AG Dor                34.188268    PACS100  100    
13    1342239416  V* AG Dor                34.188268    PACS70   70     
14    1342225244  V* AR Lac                42.771600    PACS100  100    
15    1342225244  V* AR Lac                42.771600    PACS70   70     
16    1342238095  HD 8357                  44.345898    PACS100  100    
17    1342238095  HD 8357                  44.345898    PACS70   70     
18    1342245708  V* AS Dra                43.000765    PACS100  100    
19    1342245708  V* AS Dra                43.000765    PACS70   70     
20    1342196038  V* AU Mic                9.909821     PACS100  100    
21    1342196038  V* AU Mic                9.909821     PACS70   70     
22    1342223909  BD+20 307                118.203310   PACS100  100    
23    1342223909  BD+20 307                118.203310   PACS70   70     
24    1342225451  BD+47 3700               566.572238   PACS100  100    
25    1342225451  BD+47 3700               566.572238   PACS70   70     
26    1342269654  BD-19 1062               66.941125    PACS100  100    
27    1342269654  BD-19 1062               66.941125    PACS70   70     
28    1342269650  BD-20 951                61.685748    PACS100  100    
29    1342269650  BD-20 951                61.685748    PACS70   70     
30    1342233075  V* BH CVn                46.148237    PACS100  100    
31    1342233075  V* BH CVn                46.148237    PACS70   70     
32    1342225491  V* BK Psc                33.911640    PACS100  100    
33    1342225491  V* BK Psc                33.911640    PACS70   70     
34    1342221346  V* BP Psc                358.757265   PACS100  100    
35    1342221346  V* BP Psc                358.757265   PACS70   70     
36    1342270953  V* BW Phe                37.071637    PACS100  100    
37    1342270953  V* BW Phe                37.071637    PACS70   70     
38    1342232520  * 42 Cap                 35.232730    PACS100  100    
39    1342232520  * 42 Cap                 35.232730    PACS70   70     
40    1342225409  CD-30 11814              514.218131   PACS100  100    
41    1342225409  CD-30 11814              514.218131   PACS70   70     
42    1342269256  CD-30 2310               67.007961    PACS100  100    
43    1342269256  CD-30 2310               67.007961    PACS70   70     
44    1342267591  CD-31 16041              49.614742    PACS100  100    
45    1342267591  CD-31 16041              49.614742    PACS70   70     
46    1342269648  CD-36 1785               87.768572    PACS100  100    
47    1342269648  CD-36 1785               87.768572    PACS70   70     
48    1342265518  CD-42 2906               88.865981    PACS100  100    
49    1342265518  CD-42 2906               88.865981    PACS70   70     
50    1342269658  CD-43 3604               95.266221    PACS100  100    
51    1342269658  CD-43 3604               95.266221    PACS70   70     
52    1342269250  CD-52 1363               134.044664   PACS100  100    
53    1342269250  CD-52 1363               134.044664   PACS70   70  

### Left join the path table onto the input table

The rows of the resulting table will be the same as that of the input table, with a path column added.

In [10]:
merged = pd.merge(df_in, df_paths, how = 'left', on = 'obsid')

In [11]:
#look at the merged table
merged

obsid                      xid      dist_pc   filter  wave  \
0     1342231387  * 19 LMi                 28.809477    PACS100  100    
1     1342231387  * 19 LMi                 28.809477    PACS70   70     
2     1342237460  * 29 Ari                 28.688807    PACS100  100    
3     1342237460  * 29 Ari                 28.688807    PACS70   70     
4     1342233372  2MASS J08101691-4856291  5055.611729  PACS100  100    
5     1342233372  2MASS J08101691-4856291  5055.611729  PACS70   70     
6     1342265601  CD-54 4621               110.619469   PACS100  100    
7     1342265601  CD-54 4621               110.619469   PACS70   70     
8     1342265609  CD-52 5008               137.741047   PACS100  100    
9     1342265609  CD-52 5008               137.741047   PACS70   70     
10    1342224188  TWA 26                   49.666490    PACS100  100    
11    1342224188  TWA 26                   49.666490    PACS70   70     
12    1342239416  V* AG Dor                34.188268    PACS100  100    
13    1342239416  V* AG Dor                34.188268    PACS70   70     
14    1342225244  V* AR Lac                42.771600    PACS100  100    
15    1342225244  V* AR Lac                42.771600    PACS70   70     
16    1342238095  HD 8357                  44.345898    PACS100  100    
17    1342238095  HD 8357                  44.345898    PACS70   70     
18    1342245708  V* AS Dra                43.000765    PACS100  100    
19    1342245708  V* AS Dra                43.000765    PACS70   70     
20    1342196038  V* AU Mic                9.909821     PACS100  100    
21    1342196038  V* AU Mic                9.909821     PACS70   70     
22    1342223909  BD+20 307                118.203310   PACS100  100    
23    1342223909  BD+20 307                118.203310   PACS70   70     
24    1342225451  BD+47 3700               566.572238   PACS100  100    
25    1342225451  BD+47 3700               566.572238   PACS70   70     
26    1342269654  BD-19 1062               66.941125    PACS100  100    
27    1342269654  BD-19 1062               66.941125    PACS70   70     
28    1342269650  BD-20 951                61.685748    PACS100  100    
29    1342269650  BD-20 951                61.685748    PACS70   70     
30    1342233075  V* BH CVn                46.148237    PACS100  100    
31    1342233075  V* BH CVn                46.148237    PACS70   70     
32    1342225491  V* BK Psc                33.911640    PACS100  100    
33    1342225491  V* BK Psc                33.911640    PACS70   70     
34    1342221346  V* BP Psc                358.757265   PACS100  100    
35    1342221346  V* BP Psc                358.757265   PACS70   70     
36    1342270953  V* BW Phe                37.071637    PACS100  100    
37    1342270953  V* BW Phe                37.071637    PACS70   70     
38    1342232520  * 42 Cap                 35.232730    PACS100  100    
39    1342232520  * 42 Cap                 35.232730    PACS70   70     
40    1342225409  CD-30 11814              514.218131   PACS100  100    
41    1342225409  CD-30 11814              514.218131   PACS70   70     
42    1342269256  CD-30 2310               67.007961    PACS100  100    
43    1342269256  CD-30 2310               67.007961    PACS70   70     
44    1342267591  CD-31 16041              49.614742    PACS100  100    
45    1342267591  CD-31 16041              49.614742    PACS70   70     
46    1342269648  CD-36 1785               87.768572    PACS100  100    
47    1342269648  CD-36 1785               87.768572    PACS70   70     
48    1342265518  CD-42 2906               88.865981    PACS100  100    
49    1342265518  CD-42 2906               88.865981    PACS70   70     
50    1342269658  CD-43 3604               95.266221    PACS100  100    
51    1342269658  CD-43 3604               95.266221    PACS70   70     
52    1342269250  CD-52 1363               134.044664   PACS100  100    
53    1342269250  CD-52 1363               134.044664   PACS70   70  

In [12]:
#look at systems from the CSV for which no image was found
merged[pd.isna(merged.path)]

obsid                      xid     dist_pc   filter  wave  \
10    1342224188  TWA 26                   49.666490   PACS100  100    
11    1342224188  TWA 26                   49.666490   PACS70   70     
18    1342245708  V* AS Dra                43.000765   PACS100  100    
19    1342245708  V* AS Dra                43.000765   PACS70   70     
98    1342246704  G 263-10                 21.906477   PACS100  100    
99    1342246704  G 263-10                 21.906477   PACS70   70     
372   1342255513  V* DS Leo                11.937448   PACS100  100    
373   1342255513  V* DS Leo                11.937448   PACS70   70     
374   1342188367  HD 105                   38.476337   PACS100  100    
375   1342188367  HD 105                   38.476337   PACS70   70     
382   1342188366  HD 203                   39.385585   PACS100  100    
383   1342188366  HD 203                   39.385585   PACS70   70     
386   1342189394  * bet03 Tuc              45.558087   PACS100  100    
387   1342189394  * bet03 Tuc              45.558087   PACS70   70     
388   1342188886  HD 53842                 56.022409   PACS100  100    
389   1342188886  HD 53842                 56.022409   PACS70   70     
390   1342188485  * 49 Cet                 59.382423   PACS100  100    
391   1342188485  * 49 Cet                 59.382423   PACS70   70     
1190  1342189210  V* AG Tri                41.084634   PACS100  100    
1191  1342189210  V* AG Tri                41.084634   PACS70   70     
1954  1342238063  * nu.02 Lup              14.812620   PACS100  100    
1955  1342238063  * nu.02 Lup              14.812620   PACS70   70     
1968  1342240677  CD-46 11540              4.540501    PACS100  100    
1969  1342240677  CD-46 11540              4.540501    PACS70   70     
2106  1342193137  V* DP Tau               NaN          PACS100  100    
2107  1342193137  V* DP Tau               NaN          PACS70   70     
2110  1342193135  V* DS Tau                159.071025  PACS100  100    
2111  1342193135  V* DS Tau                159.071025  PACS70   70     
2126  1342193141  Haro 6-37               NaN          PACS100  100    
2127  1342193141  Haro 6-37               NaN          PACS70   70     
2128  1342193134  V* V397 Aur              148.599450  PACS100  100    
2129  1342193134  V* V397 Aur              148.599450  PACS70   70     
2154  1342188853  HD 100453                102.774923  PACS100  100    
2155  1342188853  HD 100453                102.774923  PACS70   70     
2156  1342188879  HD 100546                109.170306  PACS100  100    
2157  1342188879  HD 100546                109.170306  PACS70   70     
2158  1342188848  V* DX Cha                108.389334  PACS100  100    
2159  1342188848  V* DX Cha                108.389334  PACS70   70     
2176  1342193054  * c Oph                  122.697881  PACS100  100    
2177  1342193054  * c Oph                  122.697881  PACS70   70     
2196  1342193131  HD 31648                 161.773032  PACS100  100    
2197  1342193131  HD 31648                 161.773032  PACS70   70     
2200  1342193125  HD 32297                 136.239782  PACS100  100    
2201  1342193125  HD 32297                 136.239782  PACS70   70     
2216  1342188847  HD 97048                NaN          PACS100  100    
2217  1342188847  HD 97048                NaN          PACS70   70     
2236  1342189656  HD 142315                147.710487  PACS100  100    
2237  1342189656  HD 142315                147.710487  PACS70   70     
2262  1342188368  BPM 16228                41.160733   PACS100  100    
2263  1342188368  BPM 16228                41.160733   PACS70   70     
2268  1342195352  * zet Lep                21.607606   PACS100  100    
2269  1342195352  * zet Lep                21.607606   PACS70   70     
2308  1342189387  V* EP Cha               NaN          PACS100  100    
2309  1342189387  V* EP Cha               NaN          PACS70   70     
2316  1342195468  V* EK Cha               NaN      

### Clean up the final table

In [13]:
#select appropriate wavelength and remove unnecessary columns
merged = merged[(merged.wave == merged.obs_wave)][['obsid', 'xid', 'dist_pc', 'wave', 'star_jy', 'path']]

In [14]:
#convert the stellar flux into mJy, as expected by pacs_model.py
merged.star_jy *= 1000
merged.rename(columns = {"star_jy": "star_mjy"}, inplace = True)

In [15]:
#take a look at the result
merged

obsid                      xid      dist_pc  wave     star_mjy  \
1     1342231387  * 19 LMi                 28.809477    70    21.045100     
3     1342237460  * 29 Ari                 28.688807    70    11.767200     
5     1342233372  2MASS J08101691-4856291  5055.611729  70    0.036248      
6     1342265601  CD-54 4621               110.619469   100   0.249808      
8     1342265609  CD-52 5008               137.741047   100   0.326981      
13    1342239416  V* AG Dor                34.188268    70    3.080270      
15    1342225244  V* AR Lac                42.771600    70    16.488500     
17    1342238095  HD 8357                  44.345898    70    9.477410      
21    1342196038  V* AU Mic                9.909821     70    18.129000     
23    1342223909  BD+20 307                118.203310   70    0.917525      
25    1342225451  BD+47 3700               566.572238   70    0.707472      
27    1342269654  BD-19 1062               66.941125    70    0.588995      
29    1342269650  BD-20 951                61.685748    70    1.046340      
31    1342233075  V* BH CVn                46.148237    70    36.149700     
33    1342225491  V* BK Psc                33.911640    70    1.404940      
35    1342221346  V* BP Psc                358.757265   70    3.552310      
37    1342270953  V* BW Phe                37.071637    70    2.599070      
39    1342232520  * 42 Cap                 35.232730    70    32.137700     
41    1342225409  CD-30 11814              514.218131   70    0.644070      
43    1342269256  CD-30 2310               67.007961    70    0.529909      
45    1342267591  CD-31 16041              49.614742    70    1.011200      
47    1342269648  CD-36 1785               87.768572    70    0.327885      
49    1342265518  CD-42 2906               88.865981    70    0.360643      
51    1342269658  CD-43 3604               95.266221    70    0.517514      
53    1342269250  CD-52 1363               134.044664   70    0.324445      
55    1342267766  CD-52 9381               34.054610    70    1.189810      
57    1342265607  CD-54 4320               42.571307    70    1.304740      
59    1342209059  CD-64 1208               29.239766    70    4.077970      
61    1342269672  CD-78 24                 49.764118    70    0.908076      
63    1342269674  CD-86 147                63.197942    70    0.876504      
65    1342225383  V* CF Tuc                87.955389    70    5.918120      
66    1342252978  CoRoT-10                 341.658410   100   0.009160      
69    1342225367  CD-53 251                414.679660   70    0.138539      
71    1342231584  V* DY Leo                44.038119    70    3.751850      
73    1342238025  V* EO Psc                23.393783    70    6.311470      
75    1342216123  * eps Eri                3.216055     70    192.823000    
77    1342228383  * eps Aur                414.181577   70    282.106000    
79    1342211789  HD 200391                50.782301    70    4.351560      
81    1342237848  V* FF And                21.723216    70    3.759800      
83    1342211953  * alf PsA                7.703567     70    321.691000    
84    1342246681  V* ZZ Psc                17.537829    100   0.002712      
86    1342225108  GD 362                   56.246133    100   0.000210      
88    1342252011  GJ 1214                  14.553922    100   0.255641      
90    1342253029  GJ 317                   15.203483    100   1.237300      
92    1342257175  GJ 3634                  20.389854    100   0.729623      
94    1342270784  Wolf 920                 16.345211    100   0.947709      
96    1342270910  BD+40 2208               32.583904    100   1.095610      
101   1342224850  GJ 3305                 NaN           70    3.248110      
102   1342259254  GSC 02284-00503          405.959485   100   0.015355      
104   1342224186  HD 100764                301.222965   100   7.094870      
107   1342257037  HD 107146                27.464982    70    5.064740      
108   1

### Save the output

In [16]:
#'input' since this will likely be used as input to pacs_model_batch.py!
output_file = 'input/obs_path_list.csv'

In [17]:
#no need to save the indices
merged.to_csv(output_file, index = False)

## Some miscellaneous experimentation below...

In [18]:
#try joining the other way round (i.e. see which systems we have data for, but weren't in the input list)
pd.merge(df_paths, df_in, how = 'left', on = 'obsid')

obsid  obs_wave  \
0     1342186612  70         
1     1342186612  70         
2     1342186619  70         
3     1342186619  70         
4     1342187075  100        
5     1342187075  100        
6     1342187145  100        
7     1342187145  100        
8     1342188369  70         
9     1342188369  70         
10    1342188370  70         
11    1342188370  70         
12    1342188371  70         
13    1342188371  70         
14    1342188372  70         
15    1342188372  70         
16    1342188377  70         
17    1342188377  70         
18    1342188484  70         
19    1342188484  70         
20    1342188506  70         
21    1342188506  70         
22    1342188507  70         
23    1342188507  70         
24    1342188514  70         
25    1342188514  70         
26    1342188516  70         
27    1342188516  70         
28    1342188517  70         
29    1342188517  70         
30    1342188518  70         
31    1342188518  70         
32    1342188854  70         
33    1342188854  70         
34    1342188884  70         
35    1342188884  70         
36    1342188885  70         
37    1342188885  70         
38    1342188887  70         
39    1342189150  70         
40    1342189150  70         
41    1342189365  70         
42    1342189365  70         
43    1342189367  70         
44    1342189367  70         
45    1342189592  70         
46    1342189657  70         
47    1342189657  70         
48    1342189658  70         
49    1342189658  70         
50    1342189659  70         
51    1342190306  70         
52    1342190306  70         
53    1342190345  70         
54    1342190345  70         
55    1342190346  70         
56    1342190346  70         
57    1342191014  70         
58    1342191014  70         
59    1342191015  70         
60    1342191015  70         
61    1342191016  70         
62    1342191016  70         
63    1342191017  70         
64    1342191017  70         
65    1342191018  70         
66    1342191018  70         
67    1342191102  100        
68    1342191102  100        
69    1342191104  70         
70    1342192757  100        
71    1342192757  100        
72    1342192759  70         
73    1342192759  70         
74    1342192760  100        
75    1342192760  100        
76    1342192775  100        
77    1342192775  100        
78    1342193038  100        
79    1342193038  100        
80    1342193040  100        
81    1342193040  100        
82    1342193042  100        
83    1342193042  100        
84    1342193046  100        
85    1342193046  100        
86    1342193057  100        
87    1342193057  100        
88    1342193059  100        
89    1342193059  100        
90    1342193061  100        
91    1342193061  100        
92    1342193064  100        
93    1342193064  100        
94    1342193068  100        
95    1342193068  100        
96    1342193105  100        
97    1342193105  100        
98    1342193107  100        
99    1342193107  100        
100   1342193109  100        
101   1342193109  100        
102   1342193111  70         
103   1342193111  70         
104   1342193112  100        
105   1342193112  100        
106   1342193115  100        
107   1342193115  100        
108   1342193117  100        
109   1342193117  100        
110   1342193123  100        
111   1342193123  100        
112   1342193139  70         
113   1342193139  70         
114   1342193140  70         
115   1342193142  100        
116   1342193142  100        
117   1342193145  100        
118   1342193145  100        
119   1342193147  100        
120   1342193147  100        
121   1342193149  100        
122   1342193149  100        
123   1342193151  100        
124   1342193151  100        
125   1342193153  100        
126   1342193153  100        
127   1342193157  70         
128   1342193157  70         
129   1342193159  100        
130   1342193161  100        
131   1342193161  100        
132   1342193163  70 

In [19]:
#look at obsids with more than one star listed
df_in[df_in.obsid.isin(df_in.obsid.value_counts().loc[lambda x: x>2].reset_index()['index'])]

obsid          xid    dist_pc   filter  wave  model_jy   star_jy
58    1342209059  CD-64 1208   29.239766  PACS100  100   0.002019  0.002019
59    1342209059  CD-64 1208   29.239766  PACS70   70    0.004078  0.004078
100   1342224850  GJ 3305     NaN         PACS100  100   0.001605  0.001605
101   1342224850  GJ 3305     NaN         PACS70   70    0.003248  0.003248
354   1342224850  * c Eri      29.429076  PACS100  100   0.012940  0.005957
355   1342224850  * c Eri      29.429076  PACS70   70    0.023331  0.012128
1012  1342224848  * alf Cen B  1.254831   PACS100  100   0.725506  0.725506
1013  1342224848  * alf Cen B  1.254831   PACS70   70    1.471260  1.471260
2150  1342209059  HD 172555    28.546960  PACS100  100   0.089189  0.007246
2151  1342209059  HD 172555    28.546960  PACS70   70    0.192049  0.014784
2680  1342224848  * alf Cen A  1.324837   PACS100  100   1.706320  1.706320
2681  1342224848  * alf Cen A  1.324837   PACS70   70    3.459790  3.459790

In [20]:
#look for level 2 observations
for path in Path(rootdir).rglob('*/level2/HPPPMAPB/*'):
    
    full_path = path.resolve()
    print(full_path)

/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292664/1342187248/level2/HPPPMAPB/hpacs1342187248_20hpppmapb_00_1469224771737.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292666/1342187364/level2/HPPPMAPB/hpacs1342187364_20hpppmapb_00_1469228027740.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292668/1342187365/level2/HPPPMAPB/hpacs1342187365_20hpppmapb_00_1469226870160.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292670/1342187805/level2/HPPPMAPB/hpacs1342187805_20hpppmapb_00_1469231900903.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292672/1342187806/level2/HPPPMAPB/hpacs1342187806_20hpppmapb_00_1469228550974.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292674/1342187807/level2/HPPPMAPB/hpacs1342187807_20hpppmapb_00_1469231950545.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292676/1342187808/level2/HPPPMAPB/hpacs1342187808_20hpppmapb_00_1469228514727.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292678/1342187835/leve

/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292903/1342215474/level2/HPPPMAPB/hpacs1342215474_20hpppmapb_00_1469416693339.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292905/1342215476/level2/HPPPMAPB/hpacs1342215476_20hpppmapb_00_1469415173775.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292909/1342215482/level2/HPPPMAPB/hpacs1342215482_20hpppmapb_00_1469415612142.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292932/1342215623/level2/HPPPMAPB/hpacs1342215623_20hpppmapb_00_1469416636323.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292936/1342216032/level2/HPPPMAPB/hpacs1342216032_20hpppmapb_00_1469417947653.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292938/1342216034/level2/HPPPMAPB/hpacs1342216034_20hpppmapb_00_1469417434125.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292942/1342216422/level2/HPPPMAPB/hpacs1342216422_20hpppmapb_00_1469419547014.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278292945/1342216426/leve

/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278306526/1342243482/level2/HPPPMAPB/hpacs1342243482_20hpppmapb_00_1469591989843.fits.gz
/data/wyatt_archive/gkennedy/hsa/auto/AIOURL278306528/1342243483/level2/HPPPMAPB/hpacs1342243483_20hpppmapb_00_1469592092538.fits.gz
